## A.1 Import libraries

In [1]:
library(stringr)
library(leaflet)
library(dplyr)


Attaching package: ‘dplyr’

The following objects are masked from ‘package:stats’:

    filter, lag

The following objects are masked from ‘package:base’:

    intersect, setdiff, setequal, union



# 1. Built in maps

## 1.1 List providers object

In [2]:
names(providers)[c(1:5)] #Shows first 5 in provider list

[1] "OpenStreetMap"        "OpenStreetMap.Mapnik" "OpenStreetMap.DE"    
[4] "OpenStreetMap.CH"     "OpenStreetMap.France"

## 1.2 Search providers object

In [3]:
filter = str_detect(names(providers), "Esri") #Creates filter
names(providers)[filter] #Filters Esri maps

[1] "Esri"                   "Esri.WorldStreetMap"    "Esri.DeLorme"          
 [4] "Esri.WorldTopoMap"      "Esri.WorldImagery"      "Esri.WorldTerrain"     
 [7] "Esri.WorldShadedRelief" "Esri.WorldPhysical"     "Esri.OceanBasemap"     
[10] "Esri.NatGeoWorldMap"    "Esri.WorldGrayCanvas"

## 1.3. Show ESRI map

In [4]:
leaflet() %>%
  addProviderTiles("Esri")

HTML widgets cannot be represented in plain text (need html)

# 2. Mapping

## 2.1 Map 1 point with popup

In [5]:
#Enter longitude and latitude
long = -76.948270
lat = 38.983640
# Creat map
leaflet() %>% 
  addProviderTiles("CartoDB") %>% 
  addMarkers(lng = long, lat = lat, popup = 'SPP')

HTML widgets cannot be represented in plain text (need html)

## 2.2 Map from dataframe

### 2.2.1 Import dataframe

In [6]:
url = "https://assets.datacamp.com/production/repositories/1942/datasets/18a000cf70d2fe999c6a6f2b28a7dc9813730e74/ipeds.csv"
ipeds = read.csv(url)
ipeds %>% head(3)

name                                    lat      lng       sector_label
1 A T Still University of Health Sciences 40.19365 -92.58918 Private     
2 Abilene Christian University            32.46915 -99.70954 Private     
3 Abraham Baldwin Agricultural College    31.48189 -83.52828 Public

### 2.2.2 Map example 1

In [7]:
map = leaflet() %>% 
addProviderTiles("CartoDB") %>% 
addCircleMarkers(data=ipeds,
                   radius = 2, color = "red", popup=~name)
map

Assuming "lng" and "lat" are longitude and latitude, respectively


HTML widgets cannot be represented in plain text (need html)

###  2.2.3 Map example 2

In [8]:
map2 <- map %>% 
  clearMarkers() %>% 
  clearBounds()
map2 %>% 
  addCircleMarkers(data = ipeds, radius = 2, 
                   popup = ~paste0(name, "<br/>","<br/>", sector_label))


Assuming "lng" and "lat" are longitude and latitude, respectively


HTML widgets cannot be represented in plain text (need html)

### 2.2.4 Map example 3

In [9]:
# Make a color palette called pal for the values of `sector_label` using `colorFactor()`  
# Colors should be: "red", "blue", and "#9b4a11" for "Public", "Private", and "For-Profit" colleges, respectively
pal <- colorFactor(palette = c("red", "blue", "#9b4a11"), 
                   levels = c("Public", "Private", "For-Profit"))

# Add circle markers that color colleges using pal() and the values of sector_label
map2 <- 
    map %>% 
        addCircleMarkers(data = ipeds, radius = 2, 
                         color = ~pal(sector_label), 
                         label = ~paste0(name, " (", sector_label, ")"))%>% 
    addLegend(pal = pal, 
              values = c("Public", "Private", "For-Profit"))

# Print map2
map2

Assuming "lng" and "lat" are longitude and latitude, respectively


HTML widgets cannot be represented in plain text (need html)

# 3. Leaflets extras

In [10]:
library(leaflet.extras)
library(htmltools)

## 3.1 Create three dfs for type of schools

In [11]:
# Create data frame called public with only public colleges
public <- filter(ipeds, sector_label == "Public")  
profit <- filter(ipeds, sector_label == "For-Profit")  
private <- filter(ipeds, sector_label == "Private")  

## 3.2 Adding multiple map layers

In [12]:
m4 <- leaflet() %>% 

#Adding three sep maps part 1
        addTiles(group = "OSM") %>% 
        addProviderTiles("CartoDB", group = "Carto") %>% 
        addProviderTiles("Esri", group = "Esri")

## 3.3 Adding schools

In [13]:
m4  = m4 %>% addCircleMarkers(data = public, radius = 2, label = ~htmlEscape(name),
                         color = ~pal(sector_label), group = "Public") %>% #Public

        addCircleMarkers(data = private, radius = 2, label = ~htmlEscape(name),
                           color = ~pal(sector_label), group = "Private")  %>% #Private

        addCircleMarkers(data = profit, radius = 2, label = ~htmlEscape(name),
                         color = ~pal(sector_label), group = "For-Profit") #For profit

Assuming "lng" and "lat" are longitude and latitude, respectively
Assuming "lng" and "lat" are longitude and latitude, respectively
Assuming "lng" and "lat" are longitude and latitude, respectively


## 3.4 Add layer control: ability to toggle maps and groups in map

In [14]:
m4 = m4 %>% addLayersControl(baseGroups = c("OSM", "Carto", "Esri"), 
                         overlayGroups = c("Public", "Private", "For-Profit")) %>% 
        setView(lat = 39.8282, lng = -98.5795, zoom = 4) 
m4

HTML widgets cannot be represented in plain text (need html)

## 3.5 Search feature

In [17]:
# Make each sector of colleges searchable 
m4_search <- m4  %>% 
        addSearchFeatures(
            targetGroups = c("Public", "Private", "For-Profit"), 
            # Set the search zoom level to 18
            options = searchFeaturesOptions(zoom = 18)) 

# Try searching the map for a college
m4_search

HTML widgets cannot be represented in plain text (need html)

## 3.6 Cluster option

In [18]:
ipeds %>% 
    leaflet() %>% 
        addTiles() %>% 
        # Sanitize any html in our labels
        addCircleMarkers(radius = 2, label = ~htmlEscape(name),
                         # Color code colleges by sector using the `pal` color palette
                         color = ~pal(sector_label),
                         # Cluster all colleges using `clusterOptions`
                         clusterOptions = markerClusterOptions()) 

Assuming "lng" and "lat" are longitude and latitude, respectively


HTML widgets cannot be represented in plain text (need html)